# DinoV2 (Visual Analysis)

DinoV2 is a foundational model trained on loads of visual data. It's shown to be quite impressive on tasks like segmentation, depth estimation, object detection, etc.

We'll try and use this on our curated dataset to predict the success of these TikTok videos and YouTube shorts.  

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Part 1) Data Preparation

In [2]:
import pandas as pd

# Load data
train_df = pd.read_csv('train_set.csv')
validation_df = pd.read_csv('validation_set.csv')
videos_and_scores_df = pd.read_csv('videos_and_scores.csv')

# Normalize scores
train_df['virality_score_%'] /= 100
train_df['engagement_score_%'] /= 100
validation_df['virality_score_%'] /= 100
validation_df['engagement_score_%'] /= 100

train_df

Unnamed: 0     video_id  virality_score_%  engagement_score_%  \
0           1295  iHeZcp28PTw          1.000000            0.825377   
1           2562  VAv_qqxx5Dk          0.585549            0.660231   
2           2723  88uLmHImiGo          1.000000            0.740005   
3           3547  bU4YZyjj_OU          1.000000            0.698577   
4            759  jnWSiDNUspw          0.623538            0.836019   
...          ...          ...               ...                 ...   
2263         330  NAdEp9fgZz4          0.551987            0.711711   
2264        2538  hgNp8nr24kQ          0.540674            0.681448   
2265         433  TVWHk_CMLFc          0.615769            0.759859   
2266        3431  xG0fdYVdTdo          0.999990            0.703877   
2267        3762  hldyXjDi0kg          0.786502            0.809875   

                                             transcript  
0     we've done red flags but what are  potential g...  
1     I had a gentleman who in a fit of  schizophren...  
2     whoa  all right  good to see you  how you feel...  
3     I want to see a man try and buy and  that's wh...  
4     darling darling [Music]  I said I feel it in m...  
...                                                 ...  
2263  how's it been being president bro we um  sent ...  
2264  have you ever had a role where youve  really r...  
2265  God I've said I found yellow's body  right out...  
2266  he got took to the cleaners by  his wife the U...  
2267  did he tell you that he was going to get  a ha...  

[2268 rows x 5 columns]

# Loading in Model

In [ ]:
import torch

dinov2_vitl14 = torch.hub.load('facebookresearch/dinov2', 'dinov2_vitl14')
device = torch.device('cuda' if torch.cuda.is_available() else "cpu")

dinov2_vitl14.to(device)

Downloading: "https://github.com/facebookresearch/dinov2/zipball/main" to /root/.cache/torch/hub/main.zip
/root/.cache/torch/hub/facebookresearch_dinov2_main/dinov2/layers/swiglu_ffn.py:51: UserWarning: xFormers is not available (SwiGLU)
  warnings.warn("xFormers is not available (SwiGLU)")
/root/.cache/torch/hub/facebookresearch_dinov2_main/dinov2/layers/attention.py:33: UserWarning: xFormers is not available (Attention)
  warnings.warn("xFormers is not available (Attention)")
/root/.cache/torch/hub/facebookresearch_dinov2_main/dinov2/layers/block.py:40: UserWarning: xFormers is not available (Block)
  warnings.warn("xFormers is not available (Block)")
Downloading: "https://dl.fbaipublicfiles.com/dinov2/dinov2_vitl14/dinov2_vitl14_pretrain.pth" to /root/.cache/torch/hub/checkpoints/dinov2_vitl14_pretrain.pth
100%|██████████| 1.13G/1.13G [00:02<00:00, 410MB/s]


DinoVisionTransformer(
  (patch_embed): PatchEmbed(
    (proj): Conv2d(3, 1024, kernel_size=(14, 14), stride=(14, 14))
    (norm): Identity()
  )
  (blocks): ModuleList(
    (0-23): 24 x NestedTensorBlock(
      (norm1): LayerNorm((1024,), eps=1e-06, elementwise_affine=True)
      (attn): MemEffAttention(
        (qkv): Linear(in_features=1024, out_features=3072, bias=True)
        (attn_drop): Dropout(p=0.0, inplace=False)
        (proj): Linear(in_features=1024, out_features=1024, bias=True)
        (proj_drop): Dropout(p=0.0, inplace=False)
      )
      (ls1): LayerScale()
      (drop_path1): Identity()
      (norm2): LayerNorm((1024,), eps=1e-06, elementwise_affine=True)
      (mlp): Mlp(
        (fc1): Linear(in_features=1024, out_features=4096, bias=True)
        (act): GELU(approximate='none')
        (fc2): Linear(in_features=4096, out_features=1024, bias=True)
        (drop): Dropout(p=0.0, inplace=False)
      )
      (ls2): LayerScale()
      (drop_path2): Identity()
    )


In [ ]:
import torch
import cv2
from torchvision import transforms
import numpy as np
import h5py

SAVE_PATH = "/content/drive/MyDrive/DownloadedTranscriptVideos"
OUTPUT_PATH = "/content/drive/MyDrive/DinoV2"

def extract_frames(video_path, target_fps=10, batch_size=512):
    cap = cv2.VideoCapture(video_path)
    actual_fps = cap.get(cv2.CAP_PROP_FPS)
    frame_skip = round(actual_fps / target_fps)

    frames = []
    batch_frames = []
    frame_count = 0

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break
        # Only process the frame if it's the 'n-th' frame
        if frame_count % frame_skip == 0:
            frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)  # Convert BGR to RGB
            frame = preprocess_image(frame)
            batch_frames.append(frame)
            if len(batch_frames) == batch_size:
                frames.append(torch.stack(batch_frames))  # Stack and add batch of frames to list
                batch_frames = []  # Reset for next batch
        frame_count += 1

    if batch_frames:  # Add any remaining frames as a smaller batch
        frames.append(torch.stack(batch_frames))
    cap.release()
    return frames

def preprocess_image(frame):
    preprocess = transforms.Compose([
        transforms.ToPILImage(),
        transforms.Resize(256),
        transforms.CenterCrop(224),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
    ])
    return preprocess(frame)

def process_video(video_id):
    video_path = get_video_path(video_id)
    frame_batches = extract_frames(video_path)
    embeddings = []

    with torch.no_grad():
        for batch in frame_batches:
            batch = batch.to('cuda')  # Move batch to GPU
            embeddings_batch = dinov2_vitl14(batch)
            embeddings_batch = embeddings_batch.view(batch.size(0), -1)  # Flatten features
            embeddings.extend(embeddings_batch.cpu().numpy())  # Move embeddings back to CPU and convert to numpy

    # Save embeddings
    save_embeddings(video_id, embeddings)

def save_embeddings(video_id, embeddings):
    output_file = get_output_path(video_id)
    with h5py.File(output_file, 'w') as h5f:
        h5f.create_dataset('embeddings', data=np.array(embeddings))

def get_output_path(video_id):
    return OUTPUT_PATH + "/dinov2_vitl14/" + "embeddings_" + video_id + ".h5"

def get_video_path(video_id):
    return SAVE_PATH + "/video_" + video_id + ".mp4"


In [ ]:
import os
from tqdm import tqdm
import pandas as pd

videos_and_scores_df = pd.read_csv("videos_and_scores.csv")
for index, row in tqdm(videos_and_scores_df.iterrows(), total=videos_and_scores_df.shape[0]):

    embedding_path  = get_output_path(row['video_id'])

    if os.path.exists(embedding_path):
        print("Embeddings already extracted - continuing ")
        continue


    if not os.path.exists(get_video_path(row['video_id'])):
        print("Video file does not exist - continueing")
        continue

    print(f"Processing video - {row['video_id']}")
    process_video(row['video_id'])

  0%|          | 1/3545 [00:00<22:06,  2.67it/s]

Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Embeddings already extracted - continuing 
Processing video - V_6cDp7OPo4


  0%|          | 16/3545 [00:25<1:33:21,  1.59s/it]

Processing video - cStUxcZ_4vI


  0%|          | 17/3545 [00:39<2:38:21,  2.69s/it]

...

100%|█████████▉| 3543/3545 [14:44:53<00:40, 20.24s/it]

Processing video - 9VjPMIbqDnQ


100%|█████████▉| 3544/3545 [14:45:16<00:20, 20.96s/it]

Processing video - jL_Cze8wOT4


100%|██████████| 3545/3545 [14:45:31<00:00, 14.99s/it]


# More Efficient I/O Loading and Handling

To prevent having to load in 3,545 files we can batch them together reducing the amount of information we have to store.

In [3]:
import h5py
import numpy as np
import os
from tqdm import tqdm

def consolidate_embeddings(input_path, output_path, batch_size=100):
    """ Consolidates individual HDF5 files into fewer larger files. """
    files = [f for f in os.listdir(input_path) if f.endswith('.h5')]
    batch_count = len(files) // batch_size + (1 if len(files) % batch_size != 0 else 0)

    for i in range(batch_count):
        start = i * batch_size
        end = min((i + 1) * batch_size, len(files))
        current_batch = files[start:end]

        with h5py.File(f"{output_path}/batch_{i + 1}.h5", 'w') as h5f_out:
            for f in current_batch:
                video_id = f.split('.')[0]
                with h5py.File(f"{input_path}/{f}", 'r') as h5f_in:
                    data = h5f_in['embeddings']
                    h5f_out.create_dataset(video_id, data=data)

def load_and_normalize_embeddings(video_id, batch_file):
    """ Load and normalize embeddings from a consolidated batch file. """
    with h5py.File(batch_file, 'r') as h5f:
        embeddings = np.array(h5f[video_id])
        if embeddings.ndim == 3 and embeddings.shape[1] == 1:
            embeddings = embeddings.reshape(embeddings.shape[0], embeddings.shape[2])
        elif embeddings.ndim == 1:
            embeddings = embeddings.reshape(1, -1)
        return embeddings


def load_all_embeddings(input_path):
    """ Loads all embeddings from HDF5 consolidated files into memory. """
    embeddings_dict = {}
    files = [f for f in os.listdir(input_path) if f.endswith('.h5')]

    for file_name in tqdm(files, total=len(files)):
        file_path = os.path.join(input_path, file_name)
        with h5py.File(file_path, 'r') as h5f:
            # Iterate over each dataset in the HDF5 file
            for video_id in h5f.keys():
                # Load embeddings, already considering the frame skipping
                embeddings = np.array(h5f[video_id])
                embeddings_dict[video_id] = embeddings

    return embeddings_dict


MODE = "LOADING"

embeddings = {}

if MODE == "SAVING":
  consolidate_embeddings('/content/drive/MyDrive/DinoV2/dinov2_vitl14', '/content/drive/MyDrive/DinoV2/dinov2_vitl14/consolidated')

if MODE == "LOADING":
  embeddings = load_all_embeddings('/content/drive/MyDrive/DinoV2/dinov2_vitl14/consolidated')

100%|██████████| 36/36 [05:13<00:00,  8.71s/it]


In [4]:
embeddings[list(embeddings.keys())[0]].shape

(378, 1024)

In [5]:
scores = {}

for index, row in tqdm(train_df.iterrows(), total=train_df.shape[0]):
  scores[row['video_id']] = [row['virality_score_%'], row['engagement_score_%']]

for index, row in tqdm(validation_df.iterrows(), total=validation_df.shape[0]):
  scores[row['video_id']] = [row['virality_score_%'], row['engagement_score_%']]

scores

100%|██████████| 568/568 [00:00<00:00, 18363.17it/s]


{'iHeZcp28PTw': [1.0, 0.825377392535553],
 'VAv_qqxx5Dk': [0.5855492269332669, 0.6602305719563211],
 '88uLmHImiGo': [1.0, 0.7400053367048806],
 'bU4YZyjj_OU': [0.9999999993769592, 0.6985769772970672],
 'jnWSiDNUspw': [0.6235384307990319, 0.836018977281736],
 'Gncb8PYvqFY': [0.6640604279323903, 0.6721114028555681],
 'mN_jMheqrqU': [0.8360936235736163, 0.8784167349555613],
 'Xz5P3cKvmqo': [0.5093358375642284, 0.738545065564791],
 '0Ihf0hXzQgs': [0.5109845493047731, 0.6081449092442647],
 'ttYjh0QSYiU': [0.504067010161679, 0.675801536605914],
 'xhbJHgGhvts': [0.6178923869829691, 0.8373429626519395],
 '-qPbSosyxCU': [0.5065042908546853, 0.5803476290565677],
 '6QYXJZoZynI': [0.5200648938551635, 0.6310726919933313],
 '3mV8E6V4w7I': [0.5804605180371352, 0.8134266290205386],
 'USB1MX3xT2A': [1.0, 0.7751907098234486],
 'xaQK3BdL3dQ': [0.6323405160277209, 0.8584390479740239],
 'DtIXmF8kBr0': [0.5264556508942129, 0.7459359116159162],
 'nuuWH7PXceM': [0.5328608607431997, 0.6745148588624239],
 'WFfa

# Prepare Dataset

In [6]:
import torch
from torch.utils.data import Dataset, DataLoader
import numpy as np
import random

class VideoDataset(Dataset):
    def __init__(self, video_ids, embeddings, scores, max_frames):
        # Filter out empty embeddings
        self.video_ids = [vid for vid in video_ids if vid in embeddings and embeddings[vid].shape[0] != 0]
        self.embeddings = embeddings
        self.scores = scores
        self.max_frames = max_frames

    def __len__(self):
        return len(self.video_ids)

    def __getitem__(self, idx):
        video_id = self.video_ids[idx]
        video_embeddings = self.embeddings[video_id]

        # Reshape the embeddings if they have an extra middle dimension
        if video_embeddings.ndim == 3 and video_embeddings.shape[1] == 1:
            video_embeddings = video_embeddings.reshape(video_embeddings.shape[0], video_embeddings.shape[2])

        if video_embeddings.shape[0] > self.max_frames:
            start_frame = random.randint(0, video_embeddings.shape[0] - self.max_frames)
            video_embeddings = video_embeddings[start_frame:start_frame + self.max_frames]
        elif video_embeddings.shape[0] < self.max_frames:
            padding = np.zeros((self.max_frames - video_embeddings.shape[0], video_embeddings.shape[1]))
            video_embeddings = np.vstack([video_embeddings, padding])

        score = self.scores[video_id]
        return torch.tensor(video_embeddings, dtype=torch.float32), torch.tensor(score, dtype=torch.float32)

MAX_FRAMES = max([embeddings[i].shape[0] for i in embeddings.keys()])

# Filter Embedding Dictionaries
train_video_ids = set(train_df['video_id'])
validation_video_ids = set(validation_df['video_id'])

training_embeddings = {key[11:]: embeddings[key] for key in embeddings if key[11:] in train_video_ids}
validation_embeddings = {key[11:]: embeddings[key] for key in embeddings if key[11:] in validation_video_ids}


# Setup DataLoaders for training and validation data
train_dataset = VideoDataset(list(train_video_ids), training_embeddings, scores, max_frames=MAX_FRAMES)
train_dataloader = DataLoader(train_dataset, batch_size=10, shuffle=True)

validation_dataset = VideoDataset(list(validation_video_ids), validation_embeddings, scores, max_frames=MAX_FRAMES)
validation_dataloader = DataLoader(validation_dataset, batch_size=10, shuffle=False)

# Different Models

In [7]:
import torch.nn as nn

class GRUModel(nn.Module):
    def __init__(self, input_dim, hidden_dim, num_layers, num_classes):
        super(GRUModel, self).__init__()
        self.gru = nn.GRU(input_dim, hidden_dim, num_layers, batch_first=True)
        self.fc = nn.Linear(hidden_dim, num_classes)

    def forward(self, x):
        # x shape: (batch, seq, feature)
        output, _ = self.gru(x)
        # Decode the hidden state of the last time step
        output = self.fc(output[:, -1, :])
        return output

class LSTMModel(nn.Module):
    def __init__(self, input_dim, hidden_dim, num_layers, num_classes):
        super(LSTMModel, self).__init__()
        self.lstm = nn.LSTM(input_dim, hidden_dim, num_layers, batch_first=True)
        self.fc = nn.Linear(hidden_dim, num_classes)

    def forward(self, x):
        # x shape: (batch, seq, feature)
        output, (hn, cn) = self.lstm(x)
        # Decode the hidden state of the last time step
        output = self.fc(output[:, -1, :])
        return output


class SimpleTransformerModel(nn.Module):
    def __init__(self, embed_dim, num_heads, num_layers, num_classes):
        super().__init__()
        self.transformer_encoder = nn.TransformerEncoder(
            nn.TransformerEncoderLayer(d_model=embed_dim, nhead=num_heads),
            num_layers=num_layers
        )
        self.fc = nn.Linear(embed_dim, num_classes)

    def forward(self, src):
        out = self.transformer_encoder(src)
        out = self.fc(out.mean(dim=1))  # Aggregate along the temporal dimension
        return out


def get_model(model_type, input_dim, hidden_dim, num_layers, num_classes):
    if model_type == 'transformer':
        return SimpleTransformerModel(input_dim, num_heads=8, num_layers=num_layers, num_classes=num_classes)
    elif model_type == 'gru':
        return GRUModel(input_dim, hidden_dim, num_layers, num_classes)
    elif model_type == 'lstm':
        return LSTMModel(input_dim, hidden_dim, num_layers, num_classes)
    else:
        raise ValueError("Unsupported model type")


# Configuration Testing

Now that we've established the various models and the various types of functions/dataloaders let's test each one separately before running them in a batch run with WANDB to extract all the relevant components.

In [26]:
import torch
from torch.utils.data import Dataset, DataLoader
import torch.nn as nn
import torch.optim as optim
import numpy as np
import random


# Initialize model, optimizer, and loss function
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model = get_model(
    model_type="gru",
    input_dim=1024,
    hidden_dim=256,
    num_layers=3,
    num_classes=2
)

# Setup DataLoaders for training and validation data
train_dataset = VideoDataset(list(train_video_ids), training_embeddings, scores, max_frames=MAX_FRAMES)
train_dataloader = DataLoader(train_dataset, batch_size=10, shuffle=True)

validation_dataset = VideoDataset(list(validation_video_ids), validation_embeddings, scores, max_frames=MAX_FRAMES)
validation_dataloader = DataLoader(validation_dataset, batch_size=10, shuffle=False)

model = model.to(device)
optimizer = optim.Adam(model.parameters(), lr=0.001)
loss_fn = nn.MSELoss()

# Training and validation loop
num_epochs = 5  # Define the number of epochs
for epoch in range(num_epochs):
    model.train()  # Set the model to training mode
    train_loss = 0

    for videos, score in train_dataloader:
        videos = videos.to(device)
        score = score.to(device)
        optimizer.zero_grad()
        outputs = model(videos)
        loss = loss_fn(outputs, score)
        loss.backward()
        optimizer.step()
        train_loss += loss.item()

    # Average loss calculations
    train_loss /= len(train_dataloader)

    # Validation phase
    model.eval()  # Set the model to evaluation mode
    with torch.no_grad():  # Operations inside don't track history
        validation_loss = 0
        for videos, score in validation_dataloader:
            videos = videos.to(device)
            score = score.to(device)
            outputs = model(videos)
            loss = loss_fn(outputs, score)
            validation_loss += loss.item()

        validation_loss /= len(validation_dataloader)

    print(f'Epoch {epoch+1}/{num_epochs}, Train Loss: {train_loss:.4f}, Validation Loss: {validation_loss:.4f}')

Epoch 1/5, Train Loss: 0.0346, Validation Loss: 0.0241
Epoch 2/5, Train Loss: 0.0225, Validation Loss: 0.0228
Epoch 3/5, Train Loss: 0.0215, Validation Loss: 0.0238
Epoch 4/5, Train Loss: 0.0210, Validation Loss: 0.0226
Epoch 5/5, Train Loss: 0.0212, Validation Loss: 0.0262


# Hyperparam Sweep

Now we'll sweep through the various configuration of the videos using tiktok data trying to determine the performance of each model and the hyperparams that perform the best

In [8]:
!pip install wandb

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.7/6.7 MB 63.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 29.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.0/289.0 kB 37.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 10.8 MB/s eta 0:00:00


In [9]:
import wandb
wandb.login()

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [10]:
import torch
from torch.utils.data import DataLoader
import wandb

class EarlyStopping:
    def __init__(self, patience=3, min_delta=0):
        """
        Args:
            patience (int): How many epochs to wait after last time validation loss improved.
                            Default: 3
            min_delta (float): Minimum change in the monitored quantity to qualify as an improvement.
                                Default: 0
        """
        self.patience = patience
        self.min_delta = min_delta
        self.counter = 0
        self.best_loss = None
        self.early_stop = False

    def __call__(self, val_loss):
        if self.best_loss is None:
            self.best_loss = val_loss
        elif val_loss > self.best_loss - self.min_delta:
            self.counter += 1
            print(f'EarlyStopping counter: {self.counter} out of {self.patience}')
            if self.counter >= self.patience:
                self.early_stop = True
        else:
            self.best_loss = val_loss
            self.counter = 0

In [ ]:
import wandb

# Example of a sweep configuration
sweep_config = {
    'method': 'random',  # Can be grid, random, or bayesian
    'metric': {
        'name': 'validation_loss',
        'goal': 'minimize'
    },
    'parameters': {
        'model_type': {
            'values': ['transformer', 'gru', 'lstm']
        },
        'learning_rate': {
            'min': 1e-5,
            'max': 1e-1
        },
        'batch_size': {
            'values': [8, 16, 32]
        },
        'num_layers': {
            'values': [1, 2, 3]
        },
        'hidden_dim': {
            'values': [128, 256, 512]
        },
        'num_epochs': {
            'values': [5, 10, 15, 20]
        },
    }
}

def train():
    torch.cuda.empty_cache()
    with wandb.init() as run:
        config = wandb.config
        print(config)

        model = get_model(config.model_type, 1024, config.hidden_dim, config.num_layers, 2)
        device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        model.to(device)

        train_dataset = VideoDataset(list(train_video_ids), training_embeddings, scores, max_frames=MAX_FRAMES)
        train_dataloader = DataLoader(train_dataset, batch_size=config.batch_size, shuffle=True)

        validation_dataset = VideoDataset(list(validation_video_ids), validation_embeddings, scores, max_frames=MAX_FRAMES)
        validation_dataloader = DataLoader(validation_dataset, batch_size=config.batch_size, shuffle=False)

        optimizer = torch.optim.Adam(model.parameters(), lr=config.learning_rate)
        loss_fn = nn.MSELoss()
        early_stopping = EarlyStopping(patience=3, min_delta=0.01)

        for epoch in range(config.num_epochs):
            model.train()
            train_loss = 0

            for videos, score in train_dataloader:
                videos = videos.to(device)
                score = score.to(device)
                optimizer.zero_grad()
                outputs = model(videos)
                loss = loss_fn(outputs, score)
                loss.backward()
                optimizer.step()
                train_loss += loss.item()
                wandb.log({'train_loss_step': loss.item()})

            train_loss /= len(train_dataloader)

            model.eval()
            validation_loss = 0
            with torch.no_grad():
                for videos, score in validation_dataloader:
                    videos = videos.to(device)
                    score = score.to(device)
                    outputs = model(videos)
                    loss = loss_fn(outputs, score)
                    validation_loss += loss.item()
                    wandb.log({'validation_loss_step': loss.item()})

                validation_loss /= len(validation_dataloader)

            print(f'Epoch {epoch+1}/{config.num_epochs}, Train Loss: {train_loss:.4f}, Validation Loss: {validation_loss:.4f}')
            wandb.log({'train_loss': train_loss, 'validation_loss': validation_loss})

            # Check early stopping condition
            early_stopping(validation_loss)
            if early_stopping.early_stop or validation_loss != validation_loss or train_loss != train_loss:
                print("Early stopping triggered.")
                wandb.log({'early_stopping': True})
                break

        wandb.log({'final_validation_loss': validation_loss})
        wandb.finish()

    torch.cuda.empty_cache()

# Add wandb agent to run the sweeps
sweep_id = wandb.sweep(sweep_config, project='dino-v2-vitl14-visual-model-tuning', entity='sp1d5r')
wandb.agent(sweep_id, train)

Create sweep with ID: 1lyg6lad
Sweep URL: https://wandb.ai/sp1d5r/dino-v2-vitl14-visual-model-tuning/sweeps/1lyg6lad


wandb: Agent Starting Run: 08ccwy9t with config:
wandb: 	batch_size: 32
wandb: 	hidden_dim: 128
wandb: 	learning_rate: 0.015992874807924187
wandb: 	model_type: gru
wandb: 	num_epochs: 15
wandb: 	num_layers: 1
wandb: Currently logged in as: sp1d5r. Use `wandb login --relogin` to force relogin


{'batch_size': 32, 'hidden_dim': 128, 'learning_rate': 0.015992874807924187, 'model_type': 'gru', 'num_epochs': 15, 'num_layers': 1}
Epoch 1/15, Train Loss: 0.2297, Validation Loss: 0.0264
Epoch 2/15, Train Loss: 0.0216, Validation Loss: 0.0244
EarlyStopping counter: 1 out of 3
Epoch 3/15, Train Loss: 0.0222, Validation Loss: 0.0243
EarlyStopping counter: 2 out of 3
Epoch 4/15, Train Loss: 0.0208, Validation Loss: 0.0234
EarlyStopping counter: 3 out of 3
Early stopping triggered.


wandb: Agent Starting Run: qi4muq3o with config:
wandb: 	batch_size: 32
wandb: 	hidden_dim: 512
wandb: 	learning_rate: 0.02092139457391229
wandb: 	model_type: transformer
wandb: 	num_epochs: 10
wandb: 	num_layers: 2


{'batch_size': 32, 'hidden_dim': 512, 'learning_rate': 0.02092139457391229, 'model_type': 'transformer', 'num_epochs': 10, 'num_layers': 2}


...

{'batch_size': 32, 'hidden_dim': 256, 'learning_rate': 0.0034517032885566694, 'model_type': 'lstm', 'num_epochs': 20, 'num_layers': 2}
Epoch 1/20, Train Loss: 0.0537, Validation Loss: 0.0215
Epoch 2/20, Train Loss: 0.0205, Validation Loss: 0.0227
EarlyStopping counter: 1 out of 3
Epoch 3/20, Train Loss: 0.0203, Validation Loss: 0.0214
EarlyStopping counter: 2 out of 3
Epoch 4/20, Train Loss: 0.0202, Validation Loss: 0.0247
EarlyStopping counter: 3 out of 3
Early stopping triggered.


wandb: Agent Starting Run: q550kq64 with config:
wandb: 	batch_size: 16
wandb: 	hidden_dim: 128
wandb: 	learning_rate: 0.09778104516291172
wandb: 	model_type: transformer
wandb: 	num_epochs: 5
wandb: 	num_layers: 3


{'batch_size': 16, 'hidden_dim': 128, 'learning_rate': 0.09778104516291172, 'model_type': 'transformer', 'num_epochs': 5, 'num_layers': 3}
Epoch 1/5, Train Loss: 108.5025, Validation Loss: 1.6627
Epoch 2/5, Train Loss: 0.0362, Validation Loss: 1.3322
Epoch 3/5, Train Loss: 0.0423, Validation Loss: 1.1570
Epoch 4/5, Train Loss: 0.0569, Validation Loss: 1.2047
EarlyStopping counter: 1 out of 3
Epoch 5/5, Train Loss: 0.0694, Validation Loss: 2.1098
EarlyStopping counter: 2 out of 3


wandb: Agent Starting Run: ktsfbcx0 with config:
wandb: 	batch_size: 8
wandb: 	hidden_dim: 512
wandb: 	learning_rate: 0.004486774707645505
wandb: 	model_type: transformer
wandb: 	num_epochs: 5
wandb: 	num_layers: 2


{'batch_size': 8, 'hidden_dim': 512, 'learning_rate': 0.004486774707645505, 'model_type': 'transformer', 'num_epochs': 5, 'num_layers': 2}
Epoch 1/5, Train Loss: 0.5830, Validation Loss: 0.0641
Epoch 2/5, Train Loss: 0.0368, Validation Loss: 0.0406
Epoch 3/5, Train Loss: 0.0367, Validation Loss: 0.0215
